In [3]:
import os
os.listdir('../../scripts')
import sys
sys.path.append('../../Scripts')

In [4]:
from generate_signals import SignalGenerator
from preprocess_daily import DailyPreprocessor

In [3]:
inter_no = 175
Node_id = 'i0'

In [4]:
# desired result
self = SignalGenerator()
self.prepare_data()
self.process_history()
self.process_movement()
self.make_histids()
self.set_timepoints()
self.assign_red_yellow()
self.SIGTABLE

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.


inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704416690       1       1       8       4        33   
1         178     c30  1704416690       1       1       8       4         4   
2         178     c30  1704416690       2       2       7       3         1   
0         178     c30  1704416690       2       2       7       3        34   
1         178     c30  1704416690       2       2       7       3         4   
..        ...     ...         ...     ...     ...     ...     ...       ...   
2         210     u60  1704417140       3       3       7       4         1   
0         210     u60  1704417140       3       3       7       4        65   
1         210     u60  1704417140       3       3       7       4         4   
2         210     u60  1704417140       4       4       8       3         1   
237       210     u60  1704417140       4       4       8       3        19   

         state phase_sumo  
0       gggggg        0_g  
1       gggggg        0_y  
2       gggggg       1__r  
0       GGGGGG        1_g  
1       GGGGGG        1_y  
..         ...        ...  
2    ggggggggr       3__r  
0    ggggggggr        3_g  
1    ggggggggr        3_y  
2    ggggggggr       4__r  
237  ggggggggr        4_g  

[684 rows x 10 columns]

In [5]:
self = SignalGenerator()
self.prepare_data()
self.process_history()
self.process_movement()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.


In [6]:
self.merge_dfs()

In [7]:
# 4-2. histid
self.histid = self.movedur.copy()
self.histid['node_id'] = self.histid['inter_no'].map(self.inter2node)
histid_start = self.present_time - 600
self.histid = self.histid[self.histid.start_unix > histid_start]

mapping_dict = self.matching.set_index(['node_id', 'move_no'])['state'].to_dict()

for i, row in self.histid.iterrows():
    node_id = row.node_id
    move_A = row.move_A
    move_B = row.move_B
    
    # A링의 state 지정
    if (node_id, move_A) in mapping_dict:
        state_A = mapping_dict[(node_id, move_A)]
    else:
        state_A = ''.join(self.node2init[node_id])
    self.histid.at[i, 'state_A'] = state_A

    # B링의 state 지정
    if (node_id, move_B) in mapping_dict:
        state_B = mapping_dict[(node_id, move_B)]
    else:
        state_B = ''.join(self.node2init[node_id])
    self.histid.at[i, 'state_B'] = state_B    

In [8]:
self.histid

inter_no  start_unix  phas_A  phas_B  move_A  move_B  duration node_id  \
10        175  1704416540       1       1       8       4        43      i0   
11        175  1704416540       2       2       7       3        46      i0   
12        175  1704416540       3       3       6       1        33      i0   
13        175  1704416540       3       4       6       2        23      i0   
14        175  1704416540       4       4       5       2        37      i0   
..        ...         ...     ...     ...     ...     ...       ...     ...   
255       201  1704417410       1       1       8       3        33      i8   
256       201  1704417410       2       2       5       2        36      i8   
257       201  1704417410       3       3       6       2        25      i8   
258       201  1704417410       4       4       6       1        58      i8   
259       201  1704417410       5       5       7       4        18      i8   

               state_A            state_B  
10   grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
11   grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
12   grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
13   grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
14   grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
..                 ...                ...  
255   grrrrrrrgGGrgrrr   grrrrrrrgrrGgrrr  
256   grrrrrrrgrrrgrrG   grrrrrrrgrrrgGGr  
257   grrrGGGrgrrrgrrr   grrrrrrrgrrrgGGr  
258   grrrGGGrgrrrgrrr   grrrrrrGgrrrgrrr  
259   grrGrrrrgrrrgrrr   gGGrrrrrgrrrgrrr  

[203 rows x 10 columns]

In [16]:
# 4-3. histids
new_histids = []
for parent_id in self.parent_ids:
    for child_id in self.pa2ch[parent_id]:
        new_histid = self.histid.copy()[self.histid.node_id==parent_id].drop(columns=['state_A', 'state_B'])
        # new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
        for i, row in new_histid.iterrows():
            phas_A = row.phas_A
            phas_B = row.phas_B
            new_match = self.match6[self.match6.node_id==child_id]
            Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]

            # A링의 state 지정
            state_A = Arow.iloc[0].state
            new_histid.at[i, 'state_A'] = state_A

            # B링의 state 지정
            Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
            state_B = Brow.iloc[0].state
            new_histid.at[i, 'state_B'] = state_B

            new_histid.at[i, 'node_id'] = child_id
        new_histids.append(new_histid)
import pandas as pd
new_histids = pd.concat(new_histids)
self.histids = pd.concat([self.histid.copy(), new_histids])
self.histids = self.histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
self.histids = self.histids[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration', 'state_A', 'state_B']]
self.histids.query('node_id==@Node_id')

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
44        175      i0  1704416540       1       1       8       4        43   
45        175      i0  1704416540       2       2       7       3        46   
46        175      i0  1704416540       3       3       6       1        33   
47        175      i0  1704416540       3       4       6       2        23   
48        175      i0  1704416540       4       4       5       2        37   
109       175      i0  1704416720       1       1       8       4        43   
110       175      i0  1704416720       2       2       7       3        45   
111       175      i0  1704416720       3       3       6       1        33   
112       175      i0  1704416720       3       4       6       2        22   
113       175      i0  1704416720       4       4       5       2        37   
173       175      i0  1704416900       1       1       8       4        43   
174       175      i0  1704416900       2       2       7       3        45   
175       175      i0  1704416900       3       3       6       1        33   
176       175      i0  1704416900       3       4       6       2        22   
177       175      i0  1704416900       4       4       5       2        37   
244       175      i0  1704417080       1       1       8       4        43   
245       175      i0  1704417080       2       2       7       3        45   
246       175      i0  1704417080       3       3       6       1        33   
247       175      i0  1704417080       3       4       6       2        22   
248       175      i0  1704417080       4       4       5       2        37   
306       175      i0  1704417260       1       1       8       4        43   
307       175      i0  1704417260       2       2       7       3        45   
308       175      i0  1704417260       3       3       6       1        33   
309       175      i0  1704417260       3       4       6       2        22   
310       175      i0  1704417260       4       4       5       2        37   
357       175      i0  1704417420       1       1       8       4        38   
358       175      i0  1704417420       2       2       7       3        40   
359       175      i0  1704417420       3       3       6       1        29   
360       175      i0  1704417420       3       4       6       2        20   
361       175      i0  1704417420       4       4       5       2        33   

               state_A            state_B  
44   grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
45   grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
46   grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
47   grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
48   grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
109  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
110  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
111  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
112  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
113  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
173  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
174  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
175  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
176  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
177  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
244  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
245  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
246  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
247  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
248  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
306  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
307  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
308  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
309  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
310  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
357  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
358  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
359  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
360  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
361  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr

In [9]:
self.set_timepoints()

In [12]:
self.sigtable

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704418730       1       1       8       4        38   
1         178     c30  1704418730       2       2       7       3        39   
2         178     c30  1704418730       3       3       5       2        43   
3         178     c30  1704418730       4       4       6       1        22   
4         178     c30  1704418900       1       1       8       4        38   
..        ...     ...         ...     ...     ...     ...     ...       ...   
233       210     u60  1704419299       1       1       6      18        28   
234       210     u60  1704419299       1       2       6       2        15   
235       210     u60  1704419299       2       2       5       2        43   
236       210     u60  1704419299       3       3       7       4        70   
237       210     u60  1704419299       4       4       8       3        24   

       state_A    state_B  phase_sumo  
0       gggggg     gggggg           0  
1       GGGggg     gggGGG           1  
2       GGGggg     gggGGG           2  
3       GGGggg     gggGGG           3  
4       gggggg     gggggg           0  
..         ...        ...         ...  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4  

[238 rows x 11 columns]

In [73]:
# 5-2-1 helper function of 5-2
def get_red(pre_state:str, cur_state:str):
    assert len(pre_state) == len(cur_state), "cur_state, nex_state의 길이가 서로 다릅니다."
    state_r = ''
    for c, n in zip(pre_state, cur_state):
        if c == n:
            state_r += c
        elif (c == 'r') and (n == 'G'):
            state_r += 'r'
        elif (c == 'G') and (n == 'r'):
            state_r += 'r'
        else:
            raise ValueError(f"예상치 못한 신호조합: current={c}, next={n}")
    return state_r

# 5-2-2 helper function of 5-2
def get_yellow(cur_state:str, nex_state:str):
    assert len(cur_state) == len(nex_state), "cur_state, nex_state의 길이가 서로 다릅니다."
    state_y = ''
    for c, n in zip(cur_state, nex_state):
        if c == n:
            state_y += c
        elif (c == 'r') and (n == 'G'):
            state_y += 'r'
        elif (c == 'G') and (n == 'r'):
            state_y += 'y'
        else:
            raise ValueError(f"예상치 못한 신호조합: current={c}, next={n}")
    return state_y

# 5-2-3 helper function of 5-2
def cumulate(sig, alph):
    csig = [] # cumulated sig
    pre = pd.Series({f'phas_{alph}':None})

    start_time = 0
    elapsed = 0
    for i, cur in sig.iterrows():
        start_unix = cur.start_unix
        
        # pre, nex
        if i != 0:
            pre = sig.iloc[i-1]
        
        if i != len(sig) - 1:
            nex = sig.iloc[i+1]
        
        # duration
        if cur[f'phas_{alph}'] == nex[f'phas_{alph}']:
            continue
        if cur[f'phas_{alph}'] == pre[f'phas_{alph}']:
            duration = cur.duration + pre.duration
        else:
            duration = cur.duration
        start_times = []
        states = []
        phases = []

        # red
        if i != 0:
            start_time += elapsed
            start_times.append(start_time)
            states.append(get_red(pre[f'state_{alph}'], cur[f'state_{alph}']))
            phases.append(f'{cur[f"phas_{alph}"]}r')

            elapsed = cur[f'red_{alph}']

        # green
        if i == 0:
            start_time = 0
        else:
            start_time += elapsed
        start_times.append(start_time)
        states.append(cur[f'state_{alph}'])
        phases.append(f'{cur[f"phas_{alph}"]}g')
        if i == 0:
            elapsed = duration - cur[f'yellow_{alph}']
        else:
            elapsed = duration - cur[f'yellow_{alph}'] - cur[f'red_{alph}']

        # yellow
        if i != len(sig) - 1:
            start_time += elapsed
            start_times.append(start_time)
            states.append(get_yellow(cur[f'state_{alph}'], nex[f'state_{alph}']))
            phases.append(f'{cur[f"phas_{alph}"]}y')
            elapsed = cur[f'yellow_{alph}']
        sig_ = pd.DataFrame({'start_time':start_times, f'phas_{alph}':phases, f'state_{alph}':states})
        sig_['start_unix'] = start_unix
        csig.append(sig_)
    csig = pd.concat(csig).reset_index(drop=True)
    return csig

In [89]:
import time
now = time.time()
self.SIGTABLE = []
for node_id in self.sigtable.node_id.unique():
    sig = self.sigtable.query('node_id==@node_id')
    for i, row in sig.iterrows():
        inter_no = row.inter_no
        phas_A = row.phas_A
        phas_B = row.phas_B
        start_unix = row.start_unix
        prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
        red_A    = prow[f'red_A{phas_A}']
        yellow_A = prow[f'yellow_A{phas_A}']
        red_B    = prow[f'red_B{phas_B}']
        yellow_B = prow[f'yellow_B{phas_B}']
        sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B
    sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                    'phas_A':str, 'phas_B':str})
    sig = sig.drop(['move_A','move_B'], axis=1)

    sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
    sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)

    csig_A = cumulate(sig_A, 'A')
    csig_B = cumulate(sig_B, 'B')

    SIG = pd.merge(csig_A, csig_B, on=['start_time', 'start_unix'], how='outer')
    SIG = SIG.sort_values(by='start_time').reset_index(drop=True)
    SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
    SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
    SIG['phase'] = SIG['phas_A'] + "_" + SIG['phas_B']
    SIG['node_id'] = node_id
    SIG = SIG[['node_id', 'start_unix', 'start_time', 'phase', 'state_A', 'state_B']]
    SIG['duration'] = SIG['start_time'].shift(-1) - SIG['start_time']
    SIG = SIG[:-1]
    SIG['duration'] = SIG['duration'].astype(int)
    for row in SIG.itertuples():
        state = ''
        for a, b, in zip(row.state_A, row.state_B):
            if a == 'r':
                state += b
            elif b == 'r':
                state += a
            elif a == b:
                state += a
            else:
                raise ValueError(f"예상되지 않은 조합 발생: a={a}, b={b}")
        SIG.at[row.Index, 'state'] = state
    SIG = SIG.drop(columns=['start_time', 'state_A', 'state_B'])
    self.SIGTABLE.append(SIG)
self.SIGTABLE = pd.concat(self.SIGTABLE)
self.SIGTABLE
print(time.time() - now)

0.6227824687957764


In [46]:
self = DailyPreprocessor()
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2. 중간산출물을 생성합니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:14<00:00, 1200.17it/s]


2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [97]:
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:15<00:00, 1135.80it/s]


In [99]:
self.get_matches()

이동류정보 불러오는 중:   0%|          | 0/17280 [00:00<?, ?it/s]

이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:13<00:00, 1274.30it/s]


2-1. 매칭 테이블들을 생성했습니다.


In [104]:
self.initialize_state()

2-2. 비보호우회전(g)을 배정했습니다.


In [142]:
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 모든 노드들을 순회
for node in self.nodes:
    node_id = node.getID()
    # 모든 connection
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    # i번째 connection : ci
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # j번째 connection : cj
        # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
        # 그외의 경우에는 are_foes = False (g)
        for j, cj in conns:
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

# 연등교차로
for _, row in self.coord.iterrows():
    node_id = row.node_id
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if not (pd.isna(inc_edge) and pd.isna(out_edge)):
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

# 유턴교차로
for _, row in self.uturn.iterrows():
    node_id = row.child_id
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if not (pd.isna(inc_edge) and pd.isna(out_edge)):
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

self.node2init['u00']

['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g', 'g']

In [135]:
self.uturn

parent_id child_id direction condition         inc_edge         out_edge
0        i0      u00         북      좌회전시     571500487_02  571500487_01.32
1        i2      u20         북     보행신호시  571542810_01.51     571542810_02
2        i3      u30         북     보행신호시     571556452_01     571556452_02
3        i3      u31         동     보행신호시     571500475_02  571500475_01.26
4        i3      u32         서     보행신호시     571540303_02    -571540303_02
5        i6      u60         서      좌회전시     571500535_02    -571500535_02

In [108]:
self.node2init

{'c30': ['g', 'g', 'g', 'g', 'g', 'g'],
 'i0': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r'],
 'i1': ['g', 'r', 'r', 'r', 'r', 'r', 'r', 'g', 'r', 'r'],
 'i2': ['r', 'r', 'g', 'r', 'r', 'r', 'r'],
 'i3': ['g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r'],
 'i6': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i7': ['r', 'r', 'r', 'g', 'g', 'r', 'r'],
 'i8': ['g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i9': ['r', 'r', 'r', 'r'],
 'u00': ['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g', 'g'],
 'u20': ['g', 'g', 'g', 'g', 'g', 'g'],
 'u30': ['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g'],
 'u31': ['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g'],
 'u32': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'r'],
 'u60': ['g', 'g', 'g', 'g',

In [62]:
self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))

self.parent_ids = sorted(self.inter_node[self.inter_node.inter_type=='parent'].node_id.unique())
self.child_ids = sorted(self.inter_node[self.inter_node.inter_type=='child'].node_id.unique())
self.uturn_ids = sorted(self.uturn.child_id.unique())
self.coord_ids = sorted(self.coord.child_id.unique())

ch2pa = {} # child to parent
for child_id in self.child_ids:
    parent_no = self.inter_node[self.inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = self.inter_node[self.inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향


In [64]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge
    # match5에서 parent_id에 해당하는 행들을 가져옴
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan

    # condition 별로 inc_dire, out_dire_A, out_dire_B를 정함
    ind = directions.index(direction)
    if condition == "좌회전시":
        inc_dire = direction
        out_dire_A = out_dire_B = directions[(ind + 2) % len(directions)]
    elif condition == "보행신호시":
        inc_dire = directions[(ind + 2) % len(directions)]
        out_dire_A = directions[(ind - 2) % len(directions)]
        out_dire_B = directions[(ind - 2) % len(directions)]

    # (inc_dire, out_dire_A, out_dire_B) 별로 inc_edge_id, out_edge_id를 정함
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    if condition == '보행신호시':
        # 이동류번호가 17(보행신호)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
        cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    # 유턴신호의 이동류번호를 19로 부여한다.
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), 'move_no'] = 19
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), 'move_no'] = 19
    cmatches.append(cmatch)


In [63]:
import numpy as np
# 각 coordination node에 대하여 (inc_edge_id, out_edge_id) 부여
self.coord['inter_no'] = self.coord['parent_id'].map(self.node2inter)
self.coord = self.coord.rename(columns={'child_id':'node_id'})
self.coord[['inc_dir', 'out_dir', 'inc_angle','out_angle']] = np.nan
self.coord['move_no'] = 20
self.coord = self.coord[['inter_no', 'phase_no', 'ring_type', 'move_no', 'inc_dir', 'out_dir', 'inc_angle','out_angle', 'inc_edge', 'out_edge', 'node_id']]
self.coord

inter_no  phase_no ring_type  move_no  inc_dir  out_dir  inc_angle  \
0       178         1         A       20      NaN      NaN        NaN   
1       178         1         B       20      NaN      NaN        NaN   
2       178         2         A       20      NaN      NaN        NaN   
3       178         2         B       20      NaN      NaN        NaN   
4       178         3         A       20      NaN      NaN        NaN   
5       178         3         B       20      NaN      NaN        NaN   
6       178         4         A       20      NaN      NaN        NaN   
7       178         4         B       20      NaN      NaN        NaN   

   out_angle         inc_edge          out_edge node_id  
0        NaN              NaN               NaN     c30  
1        NaN              NaN               NaN     c30  
2        NaN     571542116_01  -571542116_02.96     c30  
3        NaN  571542116_02.96  571542116_02.164     c30  
4        NaN     571542116_01  -571542116_02.96     c30  
5        NaN  571542116_02.96  571542116_02.164     c30  
6        NaN     571542116_01  -571542116_02.96     c30  
7        NaN  571542116_02.96  571542116_02.164     c30

In [65]:
# display(coord)
cmatches = pd.concat(cmatches)
self.match6 = pd.concat([self.match5, cmatches, self.coord]).drop_duplicates().sort_values(by=['inter_no', 'node_id', 'phase_no', 'ring_type'])
# self.match6.to_csv(os.path.join(self.path_intermediates, 'match6.csv'))


In [94]:
self.node2init

{'c30': ['g', 'g', 'g', 'g', 'g', 'g'],
 'i0': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r'],
 'i1': ['g', 'r', 'r', 'g', 'g', 'g', 'r', 'g', 'r', 'r'],
 'i2': ['g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'i3': ['g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r'],
 'i6': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i7': ['g', 'g', 'r', 'g', 'g', 'r', 'r'],
 'i8': ['g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i9': ['g', 'g', 'g', 'g'],
 'u00': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u20': ['g', 'g', 'g', 'g', 'g', 'g'],
 'u30': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u31': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u32': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u60': ['g', 'g', 'g', 'g',

In [95]:
self.node2init = {}
node_id = 'c30'
node = self.net.getNode(node_id)

node_id = node.getID()
# 모든 connection
conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
conns = [c for c in conns if c[0] >= 0]
conns = sorted(conns, key=lambda x: x[0])
state = []
# i번째 connection : ci
for i, ci in conns:
    if ci.getTLLinkIndex() < 0:
        continue
    are_foes = False
    # j번째 connection : cj
    # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
    # 그외의 경우에는 are_foes = False (g)
    for j, cj in conns:
        # ci, cj의 합류지점이 같으면 통과
        if ci.getTo() == cj.getTo():
            continue
        # ci, cj가 상충되면 are_foes를 True로 지정.
        if node.areFoes(i, j):
            are_foes = True
            break
    state.append('r' if are_foes else 'g')
self.node2init[node_id] = state

In [96]:
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 모든 노드들을 순회
for node in self.nodes:
    node_id = node.getID()
    # 모든 connection
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    # i번째 connection : ci
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # j번째 connection : cj
        # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
        # 그외의 경우에는 are_foes = False (g)
        for j, cj in conns:
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

# 연등교차로에도 마찬가지로 신호가 부여되어 있는 경우에 r 부여
for _, row in self.coord.iterrows():
    node_id = row.node_id
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    inc_edge = self.net.getEdge(inc_edge)
    out_edge = self.net.getEdge(out_edge)
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            self.node2init[node_id][index] = 'r'


# json 파일로 저장
with open(os.path.join(self.path_intermediates, 'node2init.json'), 'w') as file:
    json.dump(self.node2init, file)


AttributeError: 'Series' object has no attribute 'inc_edge'

In [48]:
import copy
# assign signals on matching
self.matching['init_state'] = self.matching['node_id'].map(self.node2init)
self.matching['state'] = self.matching['init_state'].map(lambda x:''.join(x))
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'state']]

# assign signals on match6

self.match6 = self.match6.reset_index(drop=True)
self.match6['init_state'] = self.match6['node_id'].map(self.node2init)
self.match6['state'] = self.match6['init_state'].map(lambda x:''.join(x))

# match6의 각 행을 순회
for i, row in self.match6.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]
    if (pd.isna(inc_edge)) or (pd.isna(out_edge)):
        continue
    if (move_no != 21):
        # print(i, node_id, move_no, ''.join(state))
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
            # print(i, node_id, move_no, index, ''.join(state))
        self.match6.at[i, 'state'] = ''.join(state)

self.match6 = self.match6.dropna(subset='state')
self.match6 = self.match6.reset_index(drop=True)
self.match6 = self.match6[['inter_no', 'node_id', 'phase_no', 'ring_type', 'move_no', 'state']]
self.match6

AttributeError: 'Pandas' object has no attribute 'inc_edge'

In [146]:
node_id = 'i2'
node = self.net.getNode(node_id)
self.node2init = {}
# 모든 connection
conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
conns = [c for c in conns if c[0] >= 0]
conns = sorted(conns, key=lambda x: x[0])
state = []
# i번째 connection : ci
for i, ci in conns:
    if ci.getTLLinkIndex() < 0:
        continue
    are_foes = False
    # j번째 connection : cj
    # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
    # 그외의 경우에는 are_foes = False (g)
    for j, cj in conns:
        # ci, cj의 합류지점이 같으면 통과
        if ci.getTo() == cj.getTo():
            continue
        # ci, cj가 상충되면 are_foes를 True로 지정.
        if node.areFoes(i, j):
            are_foes = True
            break
    state.append('r' if are_foes else 'g')
self.node2init[node_id] = state
print(state)

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

['g', 'g', 'g', 'g', 'g', 'g', 'g']


KeyError: 'i0'

In [161]:
self.match4[self.match4.inter_no==177]

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
14       177         1         A        8       남       북       180       000
15       177         1         B        4       북       남       001       176
16       177         2         A        7       북       동       000       090
17       177         2         B        3       남       서       179       270
18       177         3         A       17     NaN     NaN       NaN       NaN
19       177         3         B       18     NaN     NaN       NaN       NaN
20       177         4         A        5       서       북       268       000
21       177         4         B        1       동       남       090       180

In [160]:

self.match5[self.match5.node_id=='i2']

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
14       177         1         A        8       남       북       180       000   
15       177         1         B        4       북       남       001       176   
16       177         2         A        7       북       동       000       090   
17       177         2         B        3       남       서       179       270   
18       177         3         A       17     NaN     NaN       NaN       NaN   
19       177         3         B       18     NaN     NaN       NaN       NaN   
20       177         4         A        5       서       북       268       000   
21       177         4         B        1       동       남       090       180   

         inc_edge      out_edge node_id  
14  -571542809_01  571542811_01      i2  
15   571542811_02  571542809_01      i2  
16   571542811_02  571542107_01      i2  
17  -571542809_01  571542809_01      i2  
18            NaN           NaN      i2  
19            NaN           NaN      i2  
20  -571542809_01  571542811_01      i2  
21   571542107_02  571542809_01      i2

In [151]:
self.match5[self.match5.node_id=='i2']

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
14       177         1         A        8       남       북       180       000   
15       177         1         B        4       북       남       001       176   
16       177         2         A        7       북       동       000       090   
17       177         2         B        3       남       서       179       270   
18       177         3         A       17     NaN     NaN       NaN       NaN   
19       177         3         B       18     NaN     NaN       NaN       NaN   
20       177         4         A        5       서       북       268       000   
21       177         4         B        1       동       남       090       180   

         inc_edge      out_edge node_id  
14  -571542809_01  571542811_01      i2  
15   571542811_02  571542809_01      i2  
16   571542811_02  571542107_01      i2  
17  -571542809_01  571542809_01      i2  
18            NaN           NaN      i2  
19            NaN           NaN      i2  
20  -571542809_01  571542811_01      i2  
21   571542107_02  571542809_01      i2

In [148]:
self.matching[self.matching.node_id=='i2']

inter_no  move_no inc_dir out_dir       inc_edge      out_edge node_id
19       177        1       동       남   571542107_02  571542809_01      i2
20       177        2       서       동  -571542809_01  571542107_01      i2
21       177        3       남       서  -571542809_01  571542809_01      i2
22       177        4       북       남   571542811_02  571542809_01      i2
23       177        5       서       북  -571542809_01  571542811_01      i2
24       177        6       동       서   571542107_02  571542809_01      i2
25       177        7       북       동   571542811_02  571542107_01      i2
26       177        8       남       북  -571542809_01  571542811_01      i2
27       177       21       북       서   571542811_02  571542809_01      i2
28       177       21       서       남  -571542809_01  571542809_01      i2
29       177       21       남       동  -571542809_01  571542107_01      i2
30       177       21       동       북   571542107_02  571542811_01      i2

In [163]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:16<00:00, 1053.69it/s]


In [164]:
self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))

self.parent_ids = sorted(self.inter_node[self.inter_node.inter_type=='parent'].node_id.unique())
self.child_ids = sorted(self.inter_node[self.inter_node.inter_type=='child'].node_id.unique())
self.uturn_ids = sorted(self.uturn.child_id.unique())
self.coord_ids = sorted(self.coord.child_id.unique())

ch2pa = {} # child to parent
for child_id in self.child_ids:
    parent_no = self.inter_node[self.inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = self.inter_node[self.inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향

In [165]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []

In [167]:
row = self.uturn.iloc[0]
print(row)

parent_id                 i0
child_id                 u00
direction                  북
condition               좌회전시
inc_edge        571500487_02
out_edge     571500487_01.32
Name: 0, dtype: object


In [172]:
child_id = row.child_id
parent_id = row.parent_id
direction = row.direction
condition = row.condition
inc_edge_id = row.inc_edge
out_edge_id = row.out_edge
print(child_id, parent_id)
print(direction, condition)
print(inc_edge_id, out_edge_id)

u00 i0
북 좌회전시
571500487_02 571500487_01.32


In [169]:
# match5에서 parent_id에 해당하는 행들을 가져옴
cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
cmatch['node_id'] = child_id
cmatch[['inc_edge', 'out_edge']] = np.nan
cmatch

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A        7       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   
5       175         3         B        1       동       남       090       180   
6       175         4         A        5       서       북       268       000   
7       175         4         B        2       서       동       270       090   

   inc_edge  out_edge node_id  
0       NaN       NaN     u00  
1       NaN       NaN     u00  
2       NaN       NaN     u00  
3       NaN       NaN     u00  
4       NaN       NaN     u00  
5       NaN       NaN     u00  
6       NaN       NaN     u00  
7       NaN       NaN     u00

In [173]:
# condition 별로 inc_dire, out_dire를 정함
ind = directions.index(direction)
if condition == "좌회전시":
    inc_dire = direction
    out_dire = directions[(ind + 2) % len(directions)]
elif condition == "보행신호시":
    inc_dire = directions[(ind + 2) % len(directions)]
    out_dire = directions[(ind - 2) % len(directions)]

In [174]:
print(inc_dire, out_dire)

북 동


In [177]:
# (inc_dire, out_dire) 별로 inc_edge_id, out_edge_id를 정함
cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
if condition == '보행신호시':
    # 이동류번호가 17(보행신호)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
    cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
# 유턴신호의 이동류번호를 19로 부여한다.
cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), 'move_no'] = 19

display(cmatch)

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A       19       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   
5       175         3         B        1       동       남       090       180   
6       175         4         A        5       서       북       268       000   
7       175         4         B        2       서       동       270       090   

       inc_edge         out_edge node_id  
0           NaN              NaN     u00  
1           NaN              NaN     u00  
2  571500487_02  571500487_01.32     u00  
3           NaN              NaN     u00  
4           NaN              NaN     u00  
5           NaN              NaN     u00  
6           NaN              NaN     u00  
7           NaN              NaN     u00

In [185]:
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge
    # match5에서 parent_id에 해당하는 행들을 가져옴
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan

    # condition 별로 inc_dire, out_dire를 정함
    ind = directions.index(direction)
    if condition == "좌회전시":
        inc_dire = direction
        out_dire = directions[(ind + 2) % len(directions)]
    elif condition == "보행신호시":
        inc_dire = directions[(ind + 2) % len(directions)]
        out_dire = directions[(ind - 2) % len(directions)]

    # (inc_dire, out_dire) 별로 inc_edge_id, out_edge_id를 정함
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    if condition == '보행신호시':
        # 이동류번호가 17(보행신호)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
        cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    # 유턴신호의 이동류번호를 19로 부여한다.
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), 'move_no'] = 19
    cmatches.append(cmatch)

In [191]:
pd.concat(cmatches)

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A       19       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   
5       175         3         B        1       동       남       090       180   
6       175         4         A        5       서       북       268       000   
7       175         4         B        2       서       동       270       090   
0       177         1         A        8       남       북       180       000   
1       177         1         B        4       북       남       001       176   
2       177         2         A        7       북       동       000       090   
3       177         2         B        3       남       서       179       270   
4       177         3         A       17     NaN     NaN       NaN       NaN   
5       177         3         B       18     NaN     NaN       NaN       NaN   
6       177         4         A        5       서       북       268       000   
7       177         4         B        1       동       남       090       180   
0       178         1         A        8       남       북       180       000   
1       178         1         B        4       북       남       000       180   
2       178         2         A        7       북       동       000       090   
3       178         2         B        3       남       서       180       270   
4       178         3         A        5       서       북       270       000   
5       178         3         B        2       서       동       270       090   
6       178         4         A       19       동       서       090       270   
7       178         4         B        1       동       남       090       180   
0       178         1         A       19       남       북       180       000   
1       178         1         B        4       북       남       000       180   
2       178         2         A        7       북       동       000       090   
3       178         2         B        3       남       서       180       270   
4       178         3         A        5       서       북       270       000   
5       178         3         B        2       서       동       270       090   
6       178         4         A        6       동       서       090       270   
7       178         4         B        1       동       남       090       180   
0       178         1         A        8       남       북       180       000   
1       178         1         B       19       북       남       000       180   
2       178         2         A        7       북       동       000       090   
3       178         2         B        3       남       서       180       270   
4       178         3         A        5       서       북       270       000   
5       178         3         B        2       서       동       270       090   
6       178         4         A        6       동       서       090       270   
7       178         4         B        1       동       남       090       180   
0       210         1         A        6       동       서       090       270   
1       210         1         B       18     NaN     NaN       NaN       NaN   
2       210         2         A       19       서       북       268       000   
3       210         2         B        2       서       동       270       090   
4       210         3         A        7       북       동       359       090   
5       210         3         B        4       북       남       000       180   
6       210         4         A        8       남       북       180       000   
7       210         4         B        3       남       서       180       270   

          inc_edge         out_edge node_id  
0              NaN              NaN 

In [56]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:16<00:00, 1071.54it/s]


In [57]:
import numpy as np
import pandas as pd

self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))

self.parent_ids = sorted(self.inter_node[self.inter_node.inter_type=='parent'].node_id.unique())
self.child_ids = sorted(self.inter_node[self.inter_node.inter_type=='child'].node_id.unique())
self.uturn_ids = sorted(self.uturn.child_id.unique())
self.coord_ids = sorted(self.coord.child_id.unique())

ch2pa = {} # child to parent
for child_id in self.child_ids:
    parent_no = self.inter_node[self.inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = self.inter_node[self.inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향

# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge
    # match5에서 parent_id에 해당하는 행들을 가져옴
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan

    # condition 별로 inc_dire, out_dire를 정함
    ind = directions.index(direction)
    if condition == "좌회전시":
        inc_dire = direction
        out_dire = directions[(ind + 2) % len(directions)]
    elif condition == "보행신호시":
        inc_dire = directions[(ind + 2) % len(directions)]
        out_dire = directions[(ind - 2) % len(directions)]

    # (inc_dire, out_dire) 별로 inc_edge_id, out_edge_id를 정함
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    if condition == '보행신호시':
        # 이동류번호가 17(보행신호)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
        cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    # 유턴신호의 이동류번호를 19로 부여한다.
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), 'move_no'] = 19
    print(child_id)
    display(cmatch)
    cmatches.append(cmatch)

# 각 연등교차로(coordination node)에 대하여 (inc_edge_id, out_edge_id) 부여
self.coord['inter_no'] = self.coord['parent_id'].map(self.node2inter)
self.coord = self.coord.rename(columns={'child_id':'node_id'})
self.coord[['inc_dir', 'out_dir', 'inc_angle','out_angle']] = np.nan
self.coord['move_no'] = 20
self.coord = self.coord[['inter_no', 'phase_no', 'ring_type', 'move_no', 'inc_dir', 'out_dir', 'inc_angle','out_angle', 'inc_edge', 'out_edge', 'node_id']]

# display(coord)
cmatches = pd.concat(cmatches)
self.match6 = pd.concat([self.match5, cmatches, self.coord]).drop_duplicates().sort_values(by=['inter_no', 'node_id', 'phase_no', 'ring_type'])
# self.match6.to_csv(os.path.join(self.path_intermediates, 'match6.csv'))


u00


inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A       19       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   
5       175         3         B        1       동       남       090       180   
6       175         4         A        5       서       북       268       000   
7       175         4         B        2       서       동       270       090   

       inc_edge         out_edge node_id  
0           NaN              NaN     u00  
1           NaN              NaN     u00  
2  571500487_02  571500487_01.32     u00  
3           NaN              NaN     u00  
4           NaN              NaN     u00  
5           NaN              NaN     u00  
6           NaN              NaN     u00  
7           NaN              NaN     u00

u20


inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       177         1         A        8       남       북       180       000   
1       177         1         B        4       북       남       001       176   
2       177         2         A        7       북       동       000       090   
3       177         2         B        3       남       서       179       270   
4       177         3         A       17     NaN     NaN       NaN       NaN   
5       177         3         B       18     NaN     NaN       NaN       NaN   
6       177         4         A        5       서       북       268       000   
7       177         4         B        1       동       남       090       180   

          inc_edge      out_edge node_id  
0              NaN           NaN     u20  
1              NaN           NaN     u20  
2              NaN           NaN     u20  
3              NaN           NaN     u20  
4  571542810_01.51  571542810_02     u20  
5              NaN           NaN     u20  
6              NaN           NaN     u20  
7              NaN           NaN     u20

u30


...

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       178         1         A       19       남       북       180       000   
1       178         1         B        4       북       남       000       180   
2       178         2         A        7       북       동       000       090   
3       178         2         B        3       남       서       180       270   
4       178         3         A        5       서       북       270       000   
5       178         3         B        2       서       동       270       090   
6       178         4         A        6       동       서       090       270   
7       178         4         B        1       동       남       090       180   

       inc_edge         out_edge node_id  
0  571500475_02  571500475_01.26     u31  
1           NaN              NaN     u31  
2           NaN              NaN     u31  
3           NaN              NaN     u31  
4           NaN              NaN     u31  
5           NaN              NaN     u31  
6           NaN              NaN     u31  
7           NaN              NaN     u31

u32


inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       178         1         A        8       남       북       180       000   
1       178         1         B       19       북       남       000       180   
2       178         2         A        7       북       동       000       090   
3       178         2         B        3       남       서       180       270   
4       178         3         A        5       서       북       270       000   
5       178         3         B        2       서       동       270       090   
6       178         4         A        6       동       서       090       270   
7       178         4         B        1       동       남       090       180   

       inc_edge       out_edge node_id  
0           NaN            NaN     u32  
1  571540303_02  -571540303_02     u32  
2           NaN            NaN     u32  
3           NaN            NaN     u32  
4           NaN            NaN     u32  
5           NaN            NaN     u32  
6           NaN            NaN     u32  
7           NaN            NaN     u32

u60


inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       210         1         A        6       동       서       090       270   
1       210         1         B       18     NaN     NaN       NaN       NaN   
2       210         2         A       19       서       북       268       000   
3       210         2         B        2       서       동       270       090   
4       210         3         A        7       북       동       359       090   
5       210         3         B        4       북       남       000       180   
6       210         4         A        8       남       북       180       000   
7       210         4         B        3       남       서       180       270   

       inc_edge       out_edge node_id  
0           NaN            NaN     u60  
1           NaN            NaN     u60  
2  571500535_02  -571500535_02     u60  
3           NaN            NaN     u60  
4           NaN            NaN     u60  
5           NaN            NaN     u60  
6           NaN            NaN     u60  
7           NaN            NaN     u60

In [58]:
bdf = pd.DataFrame({'inc':[1, 2, np.nan, np.nan], 'out':[105, np.nan, 5, np.nan]})
display(bdf)
display(bdf.notna())
print(bdf.notna().all(axis=1))
print(bdf.notna().all(axis=0))


inc    out
0  1.0  105.0
1  2.0    NaN
2  NaN    5.0
3  NaN    NaN

inc    out
0   True   True
1   True  False
2  False   True
3  False  False

0     True
1    False
2    False
3    False
dtype: bool
inc    False
out    False
dtype: bool


In [59]:
bdf = pd.DataFrame({'inc':[2, np.nan, np.nan], 'out':[np.nan, 5, np.nan]})
display(bdf)
# print((bdf[['inc','out']].notna()))
# print((bdf[['inc','out']].notna()).all(axis=1))
# print((bdf[['inc','out']].notna()).all(axis=1).any())
print((bdf[['inc','out']].isna()))
print((bdf[['inc','out']].isna()).any(axis=1))
print(bdf[['inc','out']].isna().any(axis=1).all())

inc  out
0  2.0  NaN
1  NaN  5.0
2  NaN  NaN

     inc    out
0  False   True
1   True  False
2   True   True
0    True
1    True
2    True
dtype: bool
True


In [60]:

print(cmatch[['inc_edge','out_edge']].notna())
print((cmatch[['inc_edge','out_edge']].notna()).all(axis=1))
print((cmatch[['inc_edge','out_edge']].notna()).all(axis=1).any())

   inc_edge  out_edge
0     False     False
1     False     False
2      True      True
3     False     False
4     False     False
5     False     False
6     False     False
7     False     False
0    False
1    False
2     True
3    False
4    False
5    False
6    False
7    False
dtype: bool
True


In [61]:
cmatch[['inc_edge','out_edge']].isna().any(axis=1).all()

False

In [62]:
print(inc_dire)
print(out_dire)

서
북


In [63]:
cmatch

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       210         1         A        6       동       서       090       270   
1       210         1         B       18     NaN     NaN       NaN       NaN   
2       210         2         A       19       서       북       268       000   
3       210         2         B        2       서       동       270       090   
4       210         3         A        7       북       동       359       090   
5       210         3         B        4       북       남       000       180   
6       210         4         A        8       남       북       180       000   
7       210         4         B        3       남       서       180       270   

       inc_edge       out_edge node_id  
0           NaN            NaN     u60  
1           NaN            NaN     u60  
2  571500535_02  -571500535_02     u60  
3           NaN            NaN     u60  
4           NaN            NaN     u60  
5           NaN            NaN     u60  
6           NaN            NaN     u60  
7           NaN            NaN     u60

In [64]:
((cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire)).any()

True

In [65]:
cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire)]

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
2       210         2         A       19       서       북       268       000   

       inc_edge       out_edge node_id  
2  571500535_02  -571500535_02     u60

In [66]:
self.load_data()
self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))

self.parent_ids = sorted(self.inter_node[self.inter_node.inter_type=='parent'].node_id.unique())
self.child_ids = sorted(self.inter_node[self.inter_node.inter_type=='child'].node_id.unique())
self.uturn_ids = sorted(self.uturn.child_id.unique())
self.coord_ids = sorted(self.coord.child_id.unique())

ch2pa = {} # child to parent
for child_id in self.child_ids:
    parent_no = self.inter_node[self.inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = self.inter_node[self.inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향


1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.


1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


In [67]:
row = self.uturn.iloc[0]

child_id = row.child_id
parent_id = row.parent_id
direction = row.direction
condition = row.condition
inc_edge_id = row.inc_edge
out_edge_id = row.out_edge

# match5에서 parent_id에 해당하는 행들을 가져옴
cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
cmatch['node_id'] = child_id
cmatch[['inc_edge', 'out_edge']] = np.nan

display(cmatch)

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A        7       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   
5       175         3         B        1       동       남       090       180   
6       175         4         A        5       서       북       268       000   
7       175         4         B        2       서       동       270       090   

   inc_edge  out_edge node_id  
0       NaN       NaN     u00  
1       NaN       NaN     u00  
2       NaN       NaN     u00  
3       NaN       NaN     u00  
4       NaN       NaN     u00  
5       NaN       NaN     u00  
6       NaN       NaN     u00  
7       NaN       NaN     u00

In [68]:
ind = directions.index(direction)
inc_dire_right = direction
out_dire_right = directions[(ind + 2) % len(directions)]
inc_dire_pedes = directions[(ind + 2) % len(directions)]
out_dire_pedes = directions[(ind - 2) % len(directions)]

if condition == "좌회전시":
    inc_dire = inc_dire_right
    out_dire = out_dire_right
elif condition == "보행신호시":
    inc_dire = inc_dire_pedes
    out_dire = out_dire_pedes
pedes_condition = ((cmatch.inc_dir==inc_dire_pedes) & (cmatch.out_dir==out_dire_pedes)).any()
right_condition = ((cmatch.inc_dir==inc_dire_right) & (cmatch.out_dir==out_dire_right)).any()


In [69]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge
    # match5에서 parent_id에 해당하는 행들을 가져옴
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan

    # condition 별로 inc_dire, out_dire를 정함
    ind = directions.index(direction)
    if condition == "좌회전시":
        inc_dire = direction
        out_dire = directions[(ind + 2) % len(directions)]
    elif condition == "보행신호시":
        inc_dire = directions[(ind + 2) % len(directions)]
        out_dire = directions[(ind - 2) % len(directions)]

    # (inc_dire, out_dire) 별로 inc_edge_id, out_edge_id를 정함
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    if condition == '보행신호시':
        # 이동류번호가 17(보행신호이동류)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
        cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]

    # 만약 어떤 유턴신호도 배정되지 않았다면, 보행신호시 > 좌회전시 > 전적색이동류발생시 > 보행신호이동류발생시 순으로 유턴신호를 배정한다.
    uturn_not_assigned = cmatch[['inc_edge','out_edge']].isna().any(axis=1).all()
    if uturn_not_assigned:
        # 보행신호시
        inc_dire_pedes = directions[(ind + 2) % len(directions)]
        out_dire_pedes = directions[(ind - 2) % len(directions)]
        # 좌회전시
        inc_dire_right = direction
        out_dire_right = directions[(ind + 2) % len(directions)]

        # 보행신호시의 inc_dir, out_dir 존재
        pedes_exists = ((cmatch.inc_dir==inc_dire_pedes) & (cmatch.out_dir==out_dire_pedes))
        right_exists = ((cmatch.inc_dir==inc_dire_right) & (cmatch.out_dir==out_dire_right))
        all_redsigns = cmatch.move_no == 18
        crosswalk_on = cmatch.move_no == 17
        
        if pedes_exists.any():
            cmatch.loc[pedes_exists, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        elif right_exists.any():
            cmatch.loc[right_exists, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        elif all_redsigns.any():
            cmatch.loc[all_redsigns, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        elif crosswalk_on.any():
            cmatch.loc[crosswalk_on & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]

    # 유턴신호의 이동류번호를 19로 부여한다.
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire), 'move_no'] = 19


In [92]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:14<00:00, 1174.55it/s]


In [166]:
self.uturn

parent_id child_id direction condition         inc_edge         out_edge
0        i0      u00         북      좌회전시     571500487_02  571500487_01.32
1        i2      u20         북     보행신호시  571542810_01.51     571542810_02
2        i3      u30         북     보행신호시     571556452_01     571556452_02
3        i3      u31         동     보행신호시     571500475_02  571500475_01.26
4        i3      u32         서     보행신호시     571540303_02    -571540303_02
5        i6      u60         서      좌회전시     571500535_02    -571500535_02

In [227]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge

    # match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan

    # 보행신호시/좌회전시 진입/진출방향
    ind = directions.index(direction)
    inc_dire_pedes = directions[(ind + 2) % len(directions)]
    out_dire_pedes = directions[(ind - 2) % len(directions)]
    inc_dire_right = direction
    out_dire_right = directions[(ind + 2) % len(directions)]

    # 보행신호시/좌회전시 조건
    pedes_exists = (cmatch.inc_dir==inc_dire_pedes) & (cmatch.out_dir==out_dire_pedes)
    right_exists = (cmatch.inc_dir==inc_dire_right) & (cmatch.out_dir==out_dire_right)

    # 보행신호시/좌회전시 진입/진출 엣지id 배정
    ind = directions.index(direction)
    if condition == "보행신호시":
        cmatch.loc[pedes_exists, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    elif condition == "좌회전시":
        cmatch.loc[right_exists, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]

    # 신호없음이동류발생시/보행신호이동류발생시 조건
    all_redsigns = cmatch.move_no == 18
    crosswalk_on = cmatch.move_no == 17

    # 만약 어떤 유턴신호도 배정되지 않았다면
    # 신호없음이동류발생시 → 보행신호이동류발생시 → 보행신호시 → 좌회전시 순으로 진입/진출 엣지id 배정
    uturn_not_assigned = cmatch[['inc_edge','out_edge']].isna().any(axis=1).all()
    if uturn_not_assigned:
        # 신호없음이동류(18) 발생시
        if all_redsigns.any():
            cmatch.loc[all_redsigns, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        # 보행신호이동류(17) 발생시
        elif crosswalk_on.any():
            cmatch.loc[crosswalk_on & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        # 보행신호시
        elif pedes_exists.any():
            cmatch.loc[pedes_exists, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        # 좌회전시
        elif right_exists.any():
            cmatch.loc[right_exists, ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]

# 유턴신호 부여 로직
## 입력 1. `self.match5`
- 컬럼목록 : 노드id, 현시번호, 링타입, 이동류번호, 진입/진출방향, 진입/진출엣지id
- 설명 : 부모교차로에 대한 매칭정보

## 입력 2. `self.uturn`
- 컬럼목록 : 부모노드id, 자식노드id, 진입방향, 조건, 진입/진출방향
- 설명 : 유턴에 대한 정보
- 여기에서 조건이란 "좌회전시" 또는 "보행신호시" 또는 ""(지정되지 않음) 중 하나임.

## 출력 : `self.match6`
- 컬럼목록 : `self.match5와` 같음
- 설명 : 부모 및 자식교차로에 대한 매칭정보 (자식교차로 : 유턴교차로, 연등교차로)

## 유턴신호 부여 알고리즘

## 요약 :
각 유턴노드별로 `self.match5`에서 해당되는 행들을 가져오고 (이것을 `cmatch`라고 한다.)
조건별로 `cmatch`에서 해당되는 행에 진입/진출엣지id를 지정한다.      

## 상세:
각 유턴 노드에 대하여 `cmatch`를 다음과 같이 정한다.

- (1) `cmatch`
  - (1-1) 부모노드의 `self.match5`에 해당하는 데이터프레임(`cmatch`)을 가져온다.
  - (1-2) `node_id`는 자식노드id로 부여하고, 진입/진출엣지id는 `np.nan`으로 초기화한다.
- (2) 조건이 "좌회전시", "보행신호시"이면
  - (2-1) 그에 따라 진입/진출방향을 정한다. (8방위)
  - (2-2) `cmatch`에서 진입/진출방향에 대응되는 행에 진입/진출엣지id를 지정한다.
- (3) 조건이 지정되지 않았거나,
    조건이 지정되었어도 진입/진출방향에 대응되는 행이 존재하지 않으면
    보행신호이동류발생시 → 전적색이동류발생시 → 보행신호시 → 좌회전시 순으로 유턴신호를 정한다.
  - (3-1) 신호없음이동류발생시
    
    이동류번호가 18(신호없음)인 행이 cmatch에 존재하면
    해당 행에 진입/진출엣지id를 지정한다.
  - (3-2) 보행신호이동류발생시
    
    3-1에 해당하지 않고, 이동류번호가 17(보행신호이동류)인 행이 `cmatch`에 존재하며
    유턴노드 방향으로 진출하는 신호가 없으면
    해당 행에 진입/진출엣지id를 지정한다.
  - (3-3) 보행신호시
    
    3-1, 3-2에 해당하지 않고
    보행신호에 대응되는 진입/진출방향에 대한 행이 `cmatch`에 존재하면
    해당 행에 진입/진출엣지id를 지정한다.
  - (3-4) 좌회전시
    
    3-1, 3-2, 3-3에 해당하지 않고
    좌회전에 대응되는 진입/진출방향에 대한 행이 `cmatch`에 존재하면
    해당 행에 진입/진출엣지id를 지정한다.
  - (3-5) 3-1 ~ 3-4에 해당되지 않는다면 유턴신호가 지정되지 않는다.

## 이후과정:
각 유턴노드에 대한 `cmatch`들을 리스트 형태로 저장한 후 `pd.concat`하여 합친다 (`cmatches`).
연동교차로에 대해서도 비슷한 종류의 테이블을 만들어둔다. (`self.coord`, 상세 생성과정 생략)
`self.match5`, `cmatches`, `self.coord를` `pd.concat`하여 `self.match6`를 만든다.

In [7]:
self = SignalGenerator()
self.main()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.
5. 신호를 생성합니다.
6. 이슈사항을 저장합니다.
(1) 0:00:00.062696
(1-1) 0:00:00.011912
(1-2) 0:00:00.027038
(1-3) 0:00:00
(1-4) 0:00:00
(1-5) 0:00:00.023746
(2) 0:00:00.517846
(2-1) 0:00:00.083063
(2-2) 0:00:00.403649
(2-3) 0:00:00.031134
(3) 0:00:00.354969
(3-1) 0:00:00.327645
(3-2) 0:00:00.027324
(4) 0:00:00.209483
(4-1) 0:00:00.001956
(4-2) 0:00:00.015003
(4-2) 0:00:00.192524
(5) 0:00:00.814094
(5-1) 0:00:00.012088
(5-2) 0:00:00.795342
(5-3) 0:00:00.006664
(6) 0:00:00.000875
total time : 0:00:01.959963


In [10]:
self.sigtable

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704416690       1       1       8       4        38   
1         178     c30  1704416690       2       2       7       3        39   
2         178     c30  1704416690       3       3       5       2        43   
3         178     c30  1704416690       4       4       6       1        22   
4         178     c30  1704416860       1       1       8       4        38   
..        ...     ...         ...     ...     ...     ...     ...       ...   
233       210     u60  1704417140       1       1       6      18        28   
234       210     u60  1704417140       1       2       6       2        15   
235       210     u60  1704417140       2       2       5       2        43   
236       210     u60  1704417140       3       3       7       4        70   
237       210     u60  1704417140       4       4       8       3        24   

       state_A    state_B  phase_sumo  
0       rrrrrr     rrrrrr           0  
1       GGGrrr     rrrGGG           1  
2       GGGrrr     rrrGGG           2  
3       GGGrrr     rrrGGG           3  
4       rrrrrr     rrrrrr           0  
..         ...        ...         ...  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4  

[238 rows x 11 columns]

In [13]:
self.unodes

AttributeError: 'SignalGenerator' object has no attribute 'unodes'

In [14]:
self.sigtable

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704416690       1       1       8       4        38   
1         178     c30  1704416690       2       2       7       3        39   
2         178     c30  1704416690       3       3       5       2        43   
3         178     c30  1704416690       4       4       6       1        22   
4         178     c30  1704416860       1       1       8       4        38   
..        ...     ...         ...     ...     ...     ...     ...       ...   
233       210     u60  1704417140       1       1       6      18        28   
234       210     u60  1704417140       1       2       6       2        15   
235       210     u60  1704417140       2       2       5       2        43   
236       210     u60  1704417140       3       3       7       4        70   
237       210     u60  1704417140       4       4       8       3        24   

       state_A    state_B  phase_sumo  
0       rrrrrr     rrrrrr           0  
1       GGGrrr     rrrGGG           1  
2       GGGrrr     rrrGGG           2  
3       GGGrrr     rrrGGG           3  
4       rrrrrr     rrrrrr           0  
..         ...        ...         ...  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4  

[238 rows x 11 columns]

In [20]:
self = DailyPreprocessor()

In [21]:
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2. 중간산출물을 생성합니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:14<00:00, 1177.84it/s]


2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [22]:
self.uturn_ids

['u00', 'u20', 'u30', 'u31', 'u32', 'u60']

In [35]:
uid2uindex = {}
for uid in self.uturn_ids:
    states = self.match6[self.match6.node_id==uid].state.unique()
    for state in states:
        if 'G' in state:
            index = state.index('G')
            uid2uindex[uid] = index
            break

In [36]:
uid2uindex

{'u00': 4, 'u20': 2, 'u30': 4, 'u31': 4, 'u32': 7, 'u60': 8}

In [30]:

self.match6[self.match6.node_id=='u31']

inter_no node_id  phase_no ring_type  move_no     state
62       178     u31         1         A        8  ggggGggg
63       178     u31         1         B        4  ggggrggg
64       178     u31         2         A        7  ggggrggg
65       178     u31         2         B        3  ggggrggg
66       178     u31         3         A        5  ggggrggg
67       178     u31         3         B        2  ggggrggg
68       178     u31         4         A        6  ggggrggg
69       178     u31         4         B        1  ggggrggg

In [ ]:
self.match6

In [5]:
self = SignalGenerator()
self.main()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.
5. 신호를 생성합니다.
6. 이슈사항을 저장합니다.
(1) 0:00:00.063416
(1-1) 0:00:00.011400
(1-2) 0:00:00.028645
(1-3) 0:00:00
(1-4) 0:00:00
(1-5) 0:00:00.023371
(2) 0:00:00.327466
(2-1) 0:00:00.079160
(2-2) 0:00:00.229118
(2-3) 0:00:00.019188
(3) 0:00:00.271045
(3-1) 0:00:00.252066
(3-2) 0:00:00.018979
(4) 0:00:00.176595
(4-1) 0:00:00
(4-2) 0:00:00.019843
(4-2) 0:00:00.156752
(5) 0:00:00.649060
(5-1) 0:00:00.010529
(5-2) 0:00:00.634530
(5-3) 0:00:00.004001
(6) 0:00:00.000928
total time : 0:00:01.488510


In [6]:
self.sigtable

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704419070       1       1       8       4        38   
1         178     c30  1704419070       2       2       7       3        39   
2         178     c30  1704419070       3       3       5       2        43   
3         178     c30  1704419070       4       4       6       1        22   
4         178     c30  1704419240       1       1       8       4        38   
..        ...     ...         ...     ...     ...     ...     ...       ...   
233       210     u60  1704419480       1       1       6      18        28   
234       210     u60  1704419480       1       2       6       2        15   
235       210     u60  1704419480       2       2       5       2        43   
236       210     u60  1704419480       3       3       7       4        70   
237       210     u60  1704419480       4       4       8       3        24   

       state_A    state_B  phase_sumo  
0       rrrrrr     rrrrrr           0  
1       GGGrrr     rrrGGG           1  
2       GGGrrr     rrrGGG           2  
3       GGGrrr     rrrGGG           3  
4       rrrrrr     rrrrrr           0  
..         ...        ...         ...  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4  

[238 rows x 11 columns]

In [7]:
self.sigtable[self.sigtable.node_id.isin(self.uturn_ids)]

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
139       175     u00  1704419060       1       1       8       4        43   
140       175     u00  1704419060       2       2       7       3        45   
141       175     u00  1704419060       3       3       6       1        33   
142       175     u00  1704419060       3       4       6       2        22   
143       175     u00  1704419060       4       4       5       2        37   
..        ...     ...         ...     ...     ...     ...     ...       ...   
233       210     u60  1704419480       1       1       6      18        28   
234       210     u60  1704419480       1       2       6       2        15   
235       210     u60  1704419480       2       2       5       2        43   
236       210     u60  1704419480       3       3       7       4        70   
237       210     u60  1704419480       4       4       8       3        24   

       state_A    state_B  phase_sumo  
139  ggggrgggg  ggggrgggg           0  
140  ggggGgggg  ggggrgggg           1  
141  ggggrgggg  ggggrgggg           2  
142  ggggrgggg  ggggrgggg           3  
143  ggggrgggg  ggggrgggg           4  
..         ...        ...         ...  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4  

[99 rows x 11 columns]

In [40]:
A = 'abcd'
for i in range(len(A)):
    print(i, i+1)
    print(A[:i] + 'x' + A[i+1:])

0 1
xbcd
1 2
axcd
2 3
abxd
3 4
abcx


In [ ]:
self = SignalGenerator()
self.main()
import numpy as np


In [60]:
# 유턴 신호가 한번도 배정되지 않은 경우에 대해서는 유턴이동류의 신호를 항상 g로 배정
for uturn_id in self.uturn_ids:
    the_uturn = self.sigtable.node_id==uturn_id
    states = np.unique(self.sigtable[the_uturn][['state_A', 'state_B']].values)
    if not any('G' in state for state in states):
        uindex = self.uid2uindex[uturn_id]
        for i, row in self.sigtable[the_uturn].iterrows():
            self.sigtable.at[i, 'state_A'] = row.state_A[:uindex] + 'g' + row.state_A[uindex+1:]
            self.sigtable.at[i, 'state_B'] = row.state_B[:uindex] + 'g' + row.state_B[uindex+1:]

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
139       175     u00  1704416900       1       1       8       4        43   
140       175     u00  1704416900       2       2       7       3        45   
141       175     u00  1704416900       3       3       6       1        33   
142       175     u00  1704416900       3       4       6       2        22   
143       175     u00  1704416900       4       4       5       2        37   
144       175     u00  1704417080       1       1       8       4        43   
145       175     u00  1704417080       2       2       7       3        45   
146       175     u00  1704417080       3       3       6       1        33   
147       175     u00  1704417080       3       4       6       2        22   
148       175     u00  1704417080       4       4       5       2        37   
149       175     u00  1704417260       1       1       8       4        43   
150       175     u00  1704417260       2       2       7       3        45   
151       175     u00  1704417260       3       3       6       1        33   
152       175     u00  1704417260       3       4       6       2        22   
153       175     u00  1704417260       4       4       5       2        37   

       state_A    state_B  phase_sumo  
139  ggggrgggg  ggggrgggg           0  
140  ggggGgggg  ggggrgggg           1  
141  ggggrgggg  ggggrgggg           2  
142  ggggrgggg  ggggrgggg           3  
143  ggggrgggg  ggggrgggg           4  
144  ggggrgggg  ggggrgggg           0  
145  ggggGgggg  ggggrgggg           1  
146  ggggrgggg  ggggrgggg           2  
147  ggggrgggg  ggggrgggg           3  
148  ggggrgggg  ggggrgggg           4  
149  ggggrgggg  ggggrgggg           0  
150  ggggGgggg  ggggrgggg           1  
151  ggggrgggg  ggggrgggg           2  
152  ggggrgggg  ggggrgggg           3  
153  ggggrgggg  ggggrgggg           4

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
154       177     u20  1704416880       1       1       8       4        43   
155       177     u20  1704416880       2       2       7       3        27   
156       177     u20  1704416880       3       3      17      18        70   
157       177     u20  1704416880       4       4       5       1        40   
158       177     u20  1704417060       1       1       8       4        43   
159       177     u20  1704417060       2       2       7       3        27   
160       177     u20  1704417060       3       3      17      18        70   
161       177     u20  1704417060       4       4       5       1        40   
162       177     u20  1704417240       1       1       8       4        43   
163       177     u20  1704417240       2       2       7       3        27   
164       177     u20  1704417240       3       3      17      18        70   
165       177     u20  1704417240       4       4       5       1        40   
166       177     u20  1704417420       1       1       8       4        43   
167       177     u20  1704417420       2       2       7       3        27   
168       177     u20  1704417420       3       3      17      18        70   
169       177     u20  1704417420       4       4       5       1        40   

    state_A state_B  phase_sumo  
154  ggrggg  ggrggg           0  
155  ggGggg  ggrggg           1  
156  ggrggg  ggrggg           2  
157  ggrggg  ggrggg           3  
158  ggrggg  ggrggg           0  
159  ggGggg  ggrggg           1  
160  ggrggg  ggrggg           2  
161  ggrggg  ggrggg           3  
162  ggrggg  ggrggg           0  
163  ggGggg  ggrggg           1  
164  ggrggg  ggrggg           2  
165  ggrggg  ggrggg           3  
166  ggrggg  ggrggg           0  
167  ggGggg  ggrggg           1  
168  ggrggg  ggrggg           2  
169  ggrggg  ggrggg           3

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
170       178     u30  1704416860       1       1       8       4        38   
171       178     u30  1704416860       2       2       7       3        39   
172       178     u30  1704416860       3       3       5       2        43   
173       178     u30  1704416860       4       4       6       1        22   
174       178     u30  1704417029       1       1       8       4        38   
175       178     u30  1704417029       2       2       7       3        39   
176       178     u30  1704417029       3       3       5       2        43   
177       178     u30  1704417029       4       4       6       1        22   
178       178     u30  1704417199       1       1       8       4        38   
179       178     u30  1704417199       2       2       7       3        39   
180       178     u30  1704417199       3       3       5       2        43   
181       178     u30  1704417199       4       4       6       1        22   
182       178     u30  1704417369       1       1       8       4        38   
183       178     u30  1704417369       2       2       7       3        39   
184       178     u30  1704417369       3       3       5       2        43   
185       178     u30  1704417369       4       4       6       1        22   

      state_A   state_B  phase_sumo  
170  ggggrggg  ggggrggg           0  
171  ggggrggg  ggggrggg           1  
172  ggggrggg  ggggrggg           2  
173  ggggGggg  ggggrggg           3  
174  ggggrggg  ggggrggg           0  
175  ggggrggg  ggggrggg           1  
176  ggggrggg  ggggrggg           2  
177  ggggGggg  ggggrggg           3  
178  ggggrggg  ggggrggg           0  
179  ggggrggg  ggggrggg           1  
180  ggggrggg  ggggrggg           2  
181  ggggGggg  ggggrggg           3  
182  ggggrggg  ggggrggg           0  
183  ggggrggg  ggggrggg           1  
184  ggggrggg  ggggrggg           2  
185  ggggGggg  ggggrggg           3

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
186       178     u31  1704416860       1       1       8       4        38   
187       178     u31  1704416860       2       2       7       3        39   
188       178     u31  1704416860       3       3       5       2        43   
189       178     u31  1704416860       4       4       6       1        22   
190       178     u31  1704417029       1       1       8       4        38   
191       178     u31  1704417029       2       2       7       3        39   
192       178     u31  1704417029       3       3       5       2        43   
193       178     u31  1704417029       4       4       6       1        22   
194       178     u31  1704417199       1       1       8       4        38   
195       178     u31  1704417199       2       2       7       3        39   
196       178     u31  1704417199       3       3       5       2        43   
197       178     u31  1704417199       4       4       6       1        22   
198       178     u31  1704417369       1       1       8       4        38   
199       178     u31  1704417369       2       2       7       3        39   
200       178     u31  1704417369       3       3       5       2        43   
201       178     u31  1704417369       4       4       6       1        22   

      state_A   state_B  phase_sumo  
186  ggggGggg  ggggrggg           0  
187  ggggrggg  ggggrggg           1  
188  ggggrggg  ggggrggg           2  
189  ggggrggg  ggggrggg           3  
190  ggggGggg  ggggrggg           0  
191  ggggrggg  ggggrggg           1  
192  ggggrggg  ggggrggg           2  
193  ggggrggg  ggggrggg           3  
194  ggggGggg  ggggrggg           0  
195  ggggrggg  ggggrggg           1  
196  ggggrggg  ggggrggg           2  
197  ggggrggg  ggggrggg           3  
198  ggggGggg  ggggrggg           0  
199  ggggrggg  ggggrggg           1  
200  ggggrggg  ggggrggg           2  
201  ggggrggg  ggggrggg           3

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
202       178     u32  1704416860       1       1       8       4        38   
203       178     u32  1704416860       2       2       7       3        39   
204       178     u32  1704416860       3       3       5       2        43   
205       178     u32  1704416860       4       4       6       1        22   
206       178     u32  1704417029       1       1       8       4        38   
207       178     u32  1704417029       2       2       7       3        39   
208       178     u32  1704417029       3       3       5       2        43   
209       178     u32  1704417029       4       4       6       1        22   
210       178     u32  1704417199       1       1       8       4        38   
211       178     u32  1704417199       2       2       7       3        39   
212       178     u32  1704417199       3       3       5       2        43   
213       178     u32  1704417199       4       4       6       1        22   
214       178     u32  1704417369       1       1       8       4        38   
215       178     u32  1704417369       2       2       7       3        39   
216       178     u32  1704417369       3       3       5       2        43   
217       178     u32  1704417369       4       4       6       1        22   

      state_A   state_B  phase_sumo  
202  gggggggr  gggggggG           0  
203  gggggggr  gggggggr           1  
204  gggggggr  gggggggr           2  
205  gggggggr  gggggggr           3  
206  gggggggr  gggggggG           0  
207  gggggggr  gggggggr           1  
208  gggggggr  gggggggr           2  
209  gggggggr  gggggggr           3  
210  gggggggr  gggggggG           0  
211  gggggggr  gggggggr           1  
212  gggggggr  gggggggr           2  
213  gggggggr  gggggggr           3  
214  gggggggr  gggggggG           0  
215  gggggggr  gggggggr           1  
216  gggggggr  gggggggr           2  
217  gggggggr  gggggggr           3

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
218       210     u60  1704416960       1       1       6      18        28   
219       210     u60  1704416960       1       2       6       2        15   
220       210     u60  1704416960       2       2       5       2        43   
221       210     u60  1704416960       3       3       7       4        70   
222       210     u60  1704416960       4       4       8       3        24   
223       210     u60  1704417140       1       1       6      18        28   
224       210     u60  1704417140       1       2       6       2        15   
225       210     u60  1704417140       2       2       5       2        43   
226       210     u60  1704417140       3       3       7       4        70   
227       210     u60  1704417140       4       4       8       3        24   
228       210     u60  1704417320       1       1       6      18        28   
229       210     u60  1704417320       1       2       6       2        15   
230       210     u60  1704417320       2       2       5       2        43   
231       210     u60  1704417320       3       3       7       4        70   
232       210     u60  1704417320       4       4       8       3        24   
233       210     u60  1704417500       1       1       6      18        28   
234       210     u60  1704417500       1       2       6       2        15   
235       210     u60  1704417500       2       2       5       2        43   
236       210     u60  1704417500       3       3       7       4        70   
237       210     u60  1704417500       4       4       8       3        24   

       state_A    state_B  phase_sumo  
218  ggggggggr  ggggggggr           0  
219  ggggggggr  ggggggggr           1  
220  ggggggggG  ggggggggr           2  
221  ggggggggr  ggggggggr           3  
222  ggggggggr  ggggggggr           4  
223  ggggggggr  ggggggggr           0  
224  ggggggggr  ggggggggr           1  
225  ggggggggG  ggggggggr           2  
226  ggggggggr  ggggggggr           3  
227  ggggggggr  ggggggggr           4  
228  ggggggggr  ggggggggr           0  
229  ggggggggr  ggggggggr           1  
230  ggggggggG  ggggggggr           2  
231  ggggggggr  ggggggggr           3  
232  ggggggggr  ggggggggr           4  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4